In [1]:
from pathlib import Path
import csv
import struct
import wave
import pandas as pd

In [2]:
import helper

Retrieve all the wav files in the selected directory

In [3]:
wav_paths = sorted(Path(helper.directory).rglob("*.wav"))
wav_paths_relative_str = []

Just keep the relative paths

In [4]:
for path in wav_paths:
    wav_paths_relative_str.append([str(path.relative_to(helper.directory))])

Dump them in a csv

In [5]:
with open(helper.csv_name, 'w') as csv_file:
    writer = csv.writer(csv_file, delimiter=',')
    writer.writerows(wav_paths_relative_str)

Create a dataframe out of this csv

Add a class column

In [6]:
data = pd.read_csv(helper.csv_name, header=None)
data.columns = ['name']
data.head()

name
0     !paccpack/808/aaaaaaaah 808.wav
1  !paccpack/808/classic plug 808.wav
2      !paccpack/808/fav plug 808.wav
3          !paccpack/808/knee 808.wav
4         !paccpack/808/lélo 808.wav

Assign each sample containing "kick", "snare", "hat", "fx" in its path/name the corresponding class, respectively k, s, h, f

In [7]:
for c in helper.classes:
    data.loc[data['name'].str.contains(c, case=False), 'class'] = c[0]
data

name class
0             !paccpack/808/aaaaaaaah 808.wav   NaN
1          !paccpack/808/classic plug 808.wav   NaN
2              !paccpack/808/fav plug 808.wav   NaN
3                  !paccpack/808/knee 808.wav   NaN
4                 !paccpack/808/lélo 808.wav   NaN
...                                       ...   ...
50029  trap samples (k-pizza)/CERTIFICATE.wav   NaN
50030        trap samples (k-pizza)/HIHAT.wav     h
50031         trap samples (k-pizza)/KICK.wav     k
50032         trap samples (k-pizza)/LEAD.wav   NaN
50033        trap samples (k-pizza)/SNARE.wav     s

[50034 rows x 2 columns]

Drop the rows containing a NaN value and add a length column

In [8]:
data_classes = data.dropna()
data_classes["length"] = ""
data_classes

<ipython-input-8-db84141c949f>:2: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  data_classes["length"] = ""


name class length
9                  !paccpack/cool fxs/a fill from me.wav     f       
10                       !paccpack/cool fxs/beepbeep.wav     f       
11                           !paccpack/cool fxs/buzz.wav     f       
12                          !paccpack/cool fxs/crowd.wav     f       
13                !paccpack/cool fxs/dowwwwwwwwwwwwn.wav     f       
...                                                  ...   ...    ...
50011  tices - 95 SPORT DRUMKIT - volume 1/snares/zaz...     s       
50012  tices - 95 SPORT DRUMKIT - volume 1/snares/zlo...     s       
50030                   trap samples (k-pizza)/HIHAT.wav     h       
50031                    trap samples (k-pizza)/KICK.wav     k       
50033                   trap samples (k-pizza)/SNARE.wav     s       

[19619 rows x 3 columns]

In [9]:
data_classes.to_csv("/Users/rayandaod/Documents/EPFL/MA4/Semester_project/data_classes.csv", index=False)

In [10]:
import librosa
for index, row in data_classes.iterrows():
    try:
        print(row["name"])
        y, sr = librosa.load("{}/{}".format(helper.directory, row["name"]))
        row["length"] = librosa.get_duration(y, sr)
    except:
        continue

!paccpack/cool fxs/a fill from me.wav
!paccpack/cool fxs/beepbeep.wav
!paccpack/cool fxs/buzz.wav
!paccpack/cool fxs/crowd.wav
!paccpack/cool fxs/dowwwwwwwwwwwwn.wav
!paccpack/cool fxs/funky hit.wav
!paccpack/cool fxs/lowrider sound west coast mah g.wav
!paccpack/cool fxs/ouuuh.wav
!paccpack/cool fxs/piou.wav
!paccpack/cool fxs/presnare OP.wav
!paccpack/cool fxs/shoutout to my big brother.wav
!paccpack/cool fxs/switchhh.wav
!paccpack/cool fxs/toon.wav
!paccpack/cool fxs/whistle.wav
!paccpack/cool fxs/woiiinw.wav
!paccpack/cool fxs/yeee hoe.wav
!paccpack/cool fxs/youuuuuuuuuuuuuuuuuu.wav
!paccpack/hi hats and open hats/acoustic hi hat.wav
!paccpack/hi hats and open hats/charleston hi hat.wav
!paccpack/hi hats and open hats/end hi hat.wav
!paccpack/hi hats and open hats/generic hi hat.wav
!paccpack/hi hats and open hats/generic open hat.wav
!paccpack/hi hats and open hats/goat hi hat.wav
!paccpack/hi hats and open hats/light hi hat.wav
!paccpack/hi hats and open hats/lo hat.wav
!paccpack

In [11]:
data_classes = data_classes[data_classes["length"] != ""]
data_classes = data_classes[data_classes["length"] != 0]
data_classes

name class     length
9                  !paccpack/cool fxs/a fill from me.wav     f        0.6
10                       !paccpack/cool fxs/beepbeep.wav     f   0.679365
11                           !paccpack/cool fxs/buzz.wav     f   3.692336
12                          !paccpack/cool fxs/crowd.wav     f  12.923084
13                !paccpack/cool fxs/dowwwwwwwwwwwwn.wav     f   0.612517
...                                                  ...   ...        ...
50011  tices - 95 SPORT DRUMKIT - volume 1/snares/zaz...     s   0.330385
50012  tices - 95 SPORT DRUMKIT - volume 1/snares/zlo...     s   0.206939
50030                   trap samples (k-pizza)/HIHAT.wav     h    0.28127
50031                    trap samples (k-pizza)/KICK.wav     k   0.647347
50033                   trap samples (k-pizza)/SNARE.wav     s   0.872517

[19617 rows x 3 columns]

In [12]:
data_classes_length_no_loop = data_classes[data_classes["name"].str.contains("loop", case=False)==False]
data_classes_length_no_loop

name class     length
9                  !paccpack/cool fxs/a fill from me.wav     f        0.6
10                       !paccpack/cool fxs/beepbeep.wav     f   0.679365
11                           !paccpack/cool fxs/buzz.wav     f   3.692336
12                          !paccpack/cool fxs/crowd.wav     f  12.923084
13                !paccpack/cool fxs/dowwwwwwwwwwwwn.wav     f   0.612517
...                                                  ...   ...        ...
50011  tices - 95 SPORT DRUMKIT - volume 1/snares/zaz...     s   0.330385
50012  tices - 95 SPORT DRUMKIT - volume 1/snares/zlo...     s   0.206939
50030                   trap samples (k-pizza)/HIHAT.wav     h    0.28127
50031                    trap samples (k-pizza)/KICK.wav     k   0.647347
50033                   trap samples (k-pizza)/SNARE.wav     s   0.872517

[16512 rows x 3 columns]

In [13]:
data_classes_length_no_loop.to_csv("/Users/rayandaod/Documents/EPFL/MA4/Semester_project/data_classes_length_no_loop.csv", index=False)

In [14]:
kicks = data_classes_length_no_loop[data_classes_length_no_loop["class"] == "k"]
kicks = kicks[kicks["length"] >= 5]
print(len(kicks))

import IPython.display as ipd
filename = kicks.iloc[4]["name"]
print(filename)
ipd.Audio("{}/{}".format(helper.directory, filename))

35
B-Wheezy/z BW x/BWheezy808/7.24.11/Bd&Bass/DrumKick.wav


In [15]:
snares = data_classes_length_no_loop[data_classes_length_no_loop["class"] == "s"]
snares = snares[snares["length"] >= 5]
print(len(snares))

import IPython.display as ipd
filename = snares.iloc[1]["name"]
print(filename)
ipd.Audio("{}/{}".format(helper.directory, filename))

33
All about music/Samplephonics Free Welcome Pack/Analogue Witchcraft /124_A_FlamingSnare_SP.wav


In [16]:
is_fx = data_classes["class"] == "f"
data_classes[is_fx]

name class     length
9                  !paccpack/cool fxs/a fill from me.wav     f        0.6
10                       !paccpack/cool fxs/beepbeep.wav     f   0.679365
11                           !paccpack/cool fxs/buzz.wav     f   3.692336
12                          !paccpack/cool fxs/crowd.wav     f  12.923084
13                !paccpack/cool fxs/dowwwwwwwwwwwwn.wav     f   0.612517
...                                                  ...   ...        ...
49883  tices - 95 SPORT DRUMKIT - volume 1/fx/jamescr...     f   0.361633
49884  tices - 95 SPORT DRUMKIT - volume 1/fx/reverse...     f   0.714286
49885  tices - 95 SPORT DRUMKIT - volume 1/fx/rewind ...     f   2.957914
49886  tices - 95 SPORT DRUMKIT - volume 1/fx/scratch...     f   0.297642
49887  tices - 95 SPORT DRUMKIT - volume 1/fx/scratch...     f   0.773469

[5124 rows x 3 columns]

In [17]:
#for sample_rel_path in data["name"]:
import librosa
y, sr = librosa.load("/Users/rayandaod/Documents/Prod/My samples/trap samples (k-pizza)/HIHAT.wav", mono=True)

In [18]:
df

NameError: name 'df' is not defined

In [ ]:
df.sampling_rate.value_counts()

In [ ]:
df.bit_depth.value_counts()

In [ ]:
df.n_channels.value_counts()